### Load libraries and data

In [15]:
import numpy as np
import pandas as pd
from scipy import stats
from scipy.stats import f_oneway

In [16]:
df = pd.read_csv(
    "/Users/alexandralugova/Documents/GitHub/MH-old-workers/data/datasets/data_clean.csv"
)

/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_14134/990969303.py:1: DtypeWarning: Columns (5,22,48) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(


### Data volume

In [17]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 41985 entries, 0 to 41984
Data columns (total 64 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   mergeid               41985 non-null  object 
 1   wave                  41985 non-null  int64  
 2   country               41985 non-null  object 
 3   dn002_                41981 non-null  object 
 4   dn003_                41985 non-null  float64
 5   dn006_                1136 non-null   object 
 6   dn042_                41985 non-null  object 
 7   ch001_                28353 non-null  float64
 8   ep005_                41985 non-null  object 
 9   ep009_                38998 non-null  object 
 10  ep026_                41985 non-null  float64
 11  ep027_                41985 non-null  float64
 12  ep028_                41985 non-null  float64
 13  ep029_                41985 non-null  float64
 14  ep030_                41985 non-null  float64
 15  ep031_             

In [18]:
# Number of unique countries
df.country.nunique()

15

In [19]:
# Number of unique individuals
df.mergeid.nunique()

14404

In [20]:
# Volume and unique individuals by wave
df.groupby("wave").agg(
    data_length=("mergeid", "count"), unique_ids=("mergeid", "nunique")
).reset_index()

wave  data_length  unique_ids
0     1         2987        2987
1     2         8466        4550
2     4        12349        6797
3     5         1302         669
4     6        12866        6529
5     7         1228         614
6     8         2787        2787

In [21]:
# Volume and unique individuals by wave couple
df.groupby("wave_couple").agg(
    data_length=("mergeid", "count"), unique_ids=("mergeid", "nunique")
).reset_index()

wave_couple  data_length  unique_ids
0         w12         6903        5047
1         w24        10277        8240
2         w45         7291        6757
3         w56         6970        6559
4         w67         7143        6617
5         w78         3401        3260

### Age, gender and number of children

In [22]:
desc = df[["age", "gender", "nb_children"]]

desc["nb_children"] = pd.to_numeric(desc["nb_children"], errors="coerce")

bin_edges = [-1, 0, 1, 2, 4, np.inf]
bin_labels = [
    "No children",
    "1 child",
    "2 children",
    "3 or 4 children",
    "5 or more children",
]

desc["nb_children_cat"] = pd.cut(
    desc["nb_children"], bins=bin_edges, labels=bin_labels, include_lowest=True
)

desc_dummies = pd.get_dummies(
    desc.drop(columns="nb_children"), columns=["gender", "nb_children_cat"]
)


def replace_boolean_with_numeric(value):
    return int(value)


columns_to_replace = [
    col
    for col in desc_dummies.columns
    if col.startswith("gender") or col.startswith("nb_children_cat")
]
desc_dummies[columns_to_replace] = desc_dummies[columns_to_replace].applymap(
    replace_boolean_with_numeric
)

round(desc_dummies.describe(), 4)

/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_14134/730765481.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  desc["nb_children"] = pd.to_numeric(desc["nb_children"], errors="coerce")
/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_14134/730765481.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  desc["nb_children_cat"] = pd.cut(
/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_14134/730765481.py:24: FutureWarning: DataFrame.applymap has been deprecated. Use DataFram

age  gender_Female  gender_Male  nb_children_cat_No children  \
count  41985.0000     41985.0000   41985.0000                   41985.0000   
mean      56.8082         0.5049       0.4951                       0.0852   
std        3.6133         0.5000       0.5000                       0.2792   
min       50.0000         0.0000       0.0000                       0.0000   
25%       54.0000         0.0000       0.0000                       0.0000   
50%       57.0000         1.0000       0.0000                       0.0000   
75%       60.0000         1.0000       1.0000                       0.0000   
max       66.0000         1.0000       1.0000                       1.0000   

       nb_children_cat_1 child  nb_children_cat_2 children  \
count               41985.0000                  41985.0000   
mean                    0.1331                      0.3581   
std                     0.3397                      0.4794   
min                     0.0000                      0.0000   
25%                     0.0000                      0.0000   
50%                     0.0000                      0.0000   
75%                     0.0000                      1.0000   
max                     1.0000                      1.0000   

       nb_children_cat_3 or 4 children  nb_children_cat_5 or more children  
count                       41985.0000                          41985.0000  
mean                            0.2212                              0.0272  
std                             0.4151                              0.1625  
min                             0.0000                              0.0000  
25%                             0.0000                              0.0000  
50%                             0.0000                              0.0000  
75%                             0.0000                              0.0000  
max                             1.0000                              1.0000

### Job characteristics

In [23]:
desc = df[
    [
        "job_status",
        "job_passive",
        "job_active",
        "job_high_strain",
        "job_low_strain",
        "job_poor_recognition",
        "job_poor_prospects",
        "job_insecurity",
    ]
]

desc_dummies = pd.get_dummies(desc, columns=["job_status"])


def replace_boolean_with_numeric(value):
    return int(value)


columns_to_replace = [
    col for col in desc_dummies.columns if col.startswith("job_status")
]
desc_dummies[columns_to_replace] = desc_dummies[columns_to_replace].applymap(
    replace_boolean_with_numeric
)

round(desc_dummies.describe(), 4)

/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_14134/3989115370.py:10: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  desc_dummies[columns_to_replace] = desc_dummies[columns_to_replace].applymap(replace_boolean_with_numeric)


job_passive  job_active  job_high_strain  job_low_strain  \
count   41985.0000  41985.0000       41985.0000      41985.0000   
mean        0.4225      0.1769           0.1582          0.2423   
std         0.4940      0.3816           0.3649          0.4285   
min         0.0000      0.0000           0.0000          0.0000   
25%         0.0000      0.0000           0.0000          0.0000   
50%         0.0000      0.0000           0.0000          0.0000   
75%         1.0000      0.0000           0.0000          0.0000   
max         1.0000      1.0000           1.0000          1.0000   

       job_poor_recognition  job_poor_prospects  job_insecurity  \
count            41985.0000          41985.0000      41985.0000   
mean                 0.4957              0.2411          0.2061   
std                  0.5000              0.4277          0.4045   
min                  0.0000              0.0000          0.0000   
25%                  0.0000              0.0000          0.0000   
50%                  0.0000              0.0000          0.0000   
75%                  1.0000              0.0000          0.0000   
max                  1.0000              1.0000          1.0000   

       job_status_Civil servant  job_status_Don't know  job_status_Employee  \
count                41985.0000             41985.0000           41985.0000   
mean                     0.0755                 0.0003               0.3453   
std                      0.2642                 0.0176               0.4755   
min                      0.0000                 0.0000               0.0000   
25%                      0.0000                 0.0000               0.0000   
50%                      0.0000                 0.0000               0.0000   
75%                      0.0000                 0.0000               1.0000   
max                      1.0000                 1.0000               1.0000   

       job_status_Private sector employee  job_status_Public sector employee  \
count                          41985.0000                         41985.0000   
mean                               0.2315                             0.1450   
std                                0.4218                             0.3521   
min                                0.0000                             0.0000   
25%                                0.0000                             0.0000   
50%                                0.0000                             0.0000   
75%                                0.0000                             0.0000   
max                                1.0000                             1.0000   

       job_status_Refusal  job_status_Self-employed  
count          41985.0000                41985.0000  
mean               0.0001                    0.1312  
std                0.0109                    0.3376  
min                0.0000                    0.0000  
25%                0.0000                    0.0000  
50%                0.0000                    0.0000  
75%                0.0000                    0.0000  
max                1.0000                    1.0000

### Work and retirement

In [24]:
round(
    df[
        ["yrscontribution", "retirement_age", "work_horizon", "work_horizon_change"]
    ].describe(),
    4,
)

yrscontribution  retirement_age  work_horizon  work_horizon_change
count       41985.0000      41985.0000    41985.0000           41985.0000
mean           36.5731         64.0076        7.1993               0.2421
std             6.8108          1.9296        3.6565               0.4671
min            10.0000         56.0000        0.0800               0.0000
25%            33.0000         63.0000        4.0000               0.0000
50%            38.0000         65.0000        7.0000               0.0000
75%            41.0000         65.0000       10.0000               0.1700
max            56.0000         73.0000       17.0000               4.0000

In [32]:
df.groupby("country").retirement_age.describe()

count       mean       std    min    25%    50%    75%    max
country                                                                       
Austria         2148.0  62.587523  2.497185  60.00  60.00  65.00  65.00  65.00
Belgium         5111.0  64.828996  0.471609  63.00  65.00  65.00  65.00  65.00
Czech Republic  2470.0  61.100045  1.805828  56.00  59.67  61.67  62.17  68.67
Denmark         6327.0  65.075391  0.264042  65.00  65.00  65.00  65.00  66.00
Estonia         2251.0  62.490004  0.885068  61.00  62.25  62.50  63.00  65.00
France          4213.0  62.488367  2.316757  60.00  60.00  62.00  64.50  67.00
Germany         4422.0  65.176122  0.348351  65.00  65.00  65.17  65.17  67.00
Italy           3332.0  64.401801  2.462986  60.00  63.75  65.00  66.25  73.00
Luxembourg       385.0  65.488442  0.448537  65.25  65.25  65.25  65.25  66.33
Netherlands     2006.0  65.000000  0.000000  65.00  65.00  65.00  65.00  65.00
Poland           689.0  63.200290  2.515969  60.00  60.00  65.00  65.00  65.75
Portugal          92.0  66.000000  0.000000  66.00  66.00  66.00  66.00  66.00
Slovenia         864.0  60.447917  2.136060  58.00  60.00  60.00  61.00  65.00
Spain           3286.0  65.029595  0.156655  65.00  65.00  65.00  65.00  69.00
Switzerland     4389.0  64.039872  0.999319  63.00  63.00  65.00  65.00  65.00

### Mental health

In [25]:
round(df[["eurod", "eurodcat", "affective_suffering", "motivation_lack"]].describe(), 4)

eurod    eurodcat  affective_suffering  motivation_lack
count  41985.0000  41985.0000           41985.0000       41985.0000
mean       1.8716      0.1808               0.2959           0.1364
std        1.8719      0.3848               0.4565           0.3432
min        0.0000      0.0000               0.0000           0.0000
25%        0.0000      0.0000               0.0000           0.0000
50%        1.0000      0.0000               0.0000           0.0000
75%        3.0000      0.0000               1.0000           0.0000
max       12.0000      1.0000               1.0000           1.0000

### ANOVA for differences in means between wave couples

In [28]:
anova_results = []

grouped = pd.get_dummies(df, columns=["gender"])


def replace_boolean_with_numeric(value):
    return int(value)


columns_to_replace = [col for col in grouped.columns if col.startswith("gender")]
grouped[columns_to_replace] = grouped[columns_to_replace].applymap(
    replace_boolean_with_numeric
)

grouped = grouped.groupby("wave_couple")

variables_to_test = [
    "age",
    "gender_Female",
    "gender_Male",
    "job_passive",
    "job_active",
    "job_high_strain",
    "job_low_strain",
    "job_poor_recognition",
    "job_poor_prospects",
    "job_insecurity",
    "yrscontribution",
    "retirement_age",
    "work_horizon",
    "work_horizon_change",
    "eurod",
    "eurodcat",
    "affective_suffering",
    "motivation_lack",
]

for var in variables_to_test:
    anova_data = [group[var].dropna() for _, group in grouped]
    f_statistic, p_value = f_oneway(*anova_data)
    anova_results.append(
        {"Variable": var, "F-statistic": f_statistic, "p-value": p_value}
    )

anova_results_df = pd.DataFrame(anova_results)

/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_14134/1606120336.py:9: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  grouped[columns_to_replace] = grouped[columns_to_replace].applymap(replace_boolean_with_numeric)


In [31]:
anova_results_df

Variable  F-statistic        p-value
0                    age  1339.703544   0.000000e+00
1          gender_Female    34.516083   2.435904e-35
2            gender_Male    34.516083   2.435904e-35
3            job_passive     4.650886   3.025237e-04
4             job_active     0.741448   5.922919e-01
5        job_high_strain     8.487215   4.851814e-08
6         job_low_strain     3.221694   6.547988e-03
7   job_poor_recognition     7.483503   4.974291e-07
8     job_poor_prospects    24.222292   1.982965e-24
9         job_insecurity    15.002700   9.532674e-15
10       yrscontribution    98.030938  4.328109e-103
11        retirement_age   474.713191   0.000000e+00
12          work_horizon   674.500583   0.000000e+00
13   work_horizon_change   700.455372   0.000000e+00
14                 eurod     8.094849   1.208194e-07
15              eurodcat     5.323718   6.790020e-05
16   affective_suffering     7.466185   5.177112e-07
17       motivation_lack     4.984920   1.445001e-04

### Depression, age and gender

In [48]:
# EuroD > 3 and job characteristics
df_dummies = pd.get_dummies(df, columns=["gender"])

means = df_dummies.groupby("eurod_group")[["age", "gender_Female"]].mean()

p_values = pd.DataFrame(index=["p-value"], columns=means.columns)

for col in means.columns:
    high_group = df_dummies[df_dummies["eurod_group"] == "High"][col]
    low_group = df_dummies[df_dummies["eurod_group"] == "Low"][col]
    t_statistic, p_value = stats.ttest_ind(high_group, low_group)
    p_values[col] = p_value

result = pd.concat([means, p_values])
result = result.round(4)
result

age  gender_Female
High     56.6073         0.5919
Low      56.9906         0.4260
p-value   0.0000         0.0000

### Depression and job characteristics

In [38]:
# EuroD > 3 and job characteristics
means = df.groupby("eurodcat")[
    [
        "job_passive",
        "job_active",
        "job_high_strain",
        "job_low_strain",
        "job_poor_recognition",
        "job_poor_prospects",
        "job_insecurity",
    ]
].mean()

p_values = pd.DataFrame(index=["p-value"], columns=means.columns)

for col in means.columns:
    high_group = df[df["eurodcat"] == 1][col]
    low_group = df[df["eurodcat"] == 0][col]
    t_statistic, p_value = stats.ttest_ind(high_group, low_group)
    p_values[col] = p_value

result = pd.concat([means, p_values])
result = result.round(4)
result

job_passive  job_active  job_high_strain  job_low_strain  \
0             0.4467      0.1570           0.1578          0.2385   
1             0.3132      0.2672           0.1601          0.2595   
p-value       0.0000      0.0000           0.6162          0.0001   

         job_poor_recognition  job_poor_prospects  job_insecurity  
0                      0.4659              0.2252          0.1927  
1                      0.6308              0.3131          0.2670  
p-value                0.0000              0.0000          0.0000

In [43]:
# EuroD and job characteristics
df["eurod_group"] = "Low"
for i in range(len(df)):
    if df["eurod"][i] >= df["eurod"].mean():
        df["eurod_group"][i] = "High"

means = df.groupby("eurod_group")[
    [
        "job_passive",
        "job_active",
        "job_high_strain",
        "job_low_strain",
        "job_poor_recognition",
        "job_poor_prospects",
        "job_insecurity",
    ]
].mean()

p_values = pd.DataFrame(index=["p-value"], columns=means.columns)

for col in means.columns:
    high_group = df[df["eurod_group"] == "High"][col]
    low_group = df[df["eurod_group"] == "Low"][col]
    t_statistic, p_value = stats.ttest_ind(high_group, low_group)
    p_values[col] = p_value

result = pd.concat([means, p_values])
result = result.round(4)
result

/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_14134/33830418.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['eurod_group'][i] = 'High'
/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_14134/33830418.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['eurod_group'][i] = 'High'
/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_14134/33830418.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  d

job_passive  job_active  job_high_strain  job_low_strain  \
High          0.3718      0.2117           0.1630          0.2535   
Low           0.4685      0.1454           0.1539          0.2322   
p-value       0.0000      0.0000           0.0106          0.0000   

         job_poor_recognition  job_poor_prospects  job_insecurity  
High                   0.5659              0.2776          0.2348  
Low                    0.4320              0.2079          0.1801  
p-value                0.0000              0.0000          0.0000

### Depression and work horizon

In [50]:
# EuroD and work horizon
means = df.groupby("eurod_group")[["work_horizon", "work_horizon_change"]].mean()

p_values = pd.DataFrame(index=["p-value"], columns=means.columns)

for col in means.columns:
    high_group = df[df["eurod_group"] == "High"][col]
    low_group = df[df["eurod_group"] == "Low"][col]
    t_statistic, p_value = stats.ttest_ind(high_group, low_group)
    p_values[col] = p_value

result = pd.concat([means, p_values])
result = result.round(4)
result

work_horizon  work_horizon_change
High           7.2860               0.2741
Low            7.1207               0.2131
p-value        0.0000               0.0000